# **THU THẬP DỮ LIỆU**
## Ý tưởng 
    Nhóm muốn thu thập thông tin về các yếu tố ảnh hưởng đến giá nhà (Bao gồm: chung cư, nhà đất, ...) tại thành phố Hồ Chí Minh
    VD: Diện tích, số phòng ngủ, phòng tắm, ... và các tiện ích liên quan
## Thực hiện
    Nhóm đã tìm được trang web khá phù hợp để thu thập dữ liệu
    'https://rever.vn'
    

In [1]:
# IMPORT THƯ VIỆN
import numpy
from bs4 import BeautifulSoup
import urllib.request
from protego import Protego
import requests
from requests import Session
import lxml
import re
import pandas as pd
from time import sleep

In [2]:
# Khởi tạo phương thức get
s = Session()
headers = {'User-Agent': 'Mozilla/5.0 (X11; Linux x86_64) '\
                         'AppleWebKit/537.36 (KHTML, like Gecko) '\
                         'Chrome/75.0.3770.80 Safari/537.36'}
# Add headers
s.headers.update(headers)
# we can use s as we do requests
# s.get(...)


#### Kiểm tra robots.txt
    Dùng thư viện protego để kiểm tra việc thu thập dữ liệu của trang web này có vi phạm không?
    Kết quả trả về True có nghĩa là được phép.

In [3]:
# kiểm tra việc thu thập
base_url = 'https://rever.vn'

r = s.get(base_url + "/robots.txt", stream=True)
rp = Protego.parse(r.text)
rp.can_fetch(base_url, "*")

True

In [4]:
# Thu thập số trang của phần mua nhà, lưu vào file csv
def get_number_of_pages(url):
    
    """
    Hàm thu thập tất cả trang web của phần mua nhà
    """
    req = s.get(url,stream=True)
    bs = BeautifulSoup(req.text, 'lxml')
    url_last = bs.findAll('a', class_ = 'btnNext')
    result = re.sub(r'\D', "", url_last[0]['href'])    
    return int(result)


page_urls = set()
num_pages = get_number_of_pages('https://rever.vn/s/ho-chi-minh/mua')

for i in range(1, num_pages+1):
    page_urls.add('https://rever.vn/s/ho-chi-minh/mua?page=' + str(i) +'&search_mode=1')
    
list_page_urls = list(page_urls)
page_urls_df = pd.DataFrame({'URL' : list_page_urls})
page_urls_df.to_csv("PAGEs_urls.csv", sep = '\t')

# Tổng số trang
pages_df = pd.read_csv('PAGEs_urls.csv', sep = '\t')
pages_df.head()

Unnamed: 0                                                URL
0           0  https://rever.vn/s/ho-chi-minh/mua?page=189&se...
1           1  https://rever.vn/s/ho-chi-minh/mua?page=18&sea...
2           2  https://rever.vn/s/ho-chi-minh/mua?page=245&se...
3           3  https://rever.vn/s/ho-chi-minh/mua?page=316&se...
4           4  https://rever.vn/s/ho-chi-minh/mua?page=179&se...

In [5]:
def crawl_house_one_page(one_page_url):
    """
    Hàm thu thập tất cả url của các căn nhà trong 1 trang
    """
    req = s.get(one_page_url,stream=True)
    bs = BeautifulSoup(req.text, 'lxml')
    list_pages = bs.findAll('div', class_ = 'group-grid__view')
        
    for house in list_pages:
        house_url = house.find('a')['href']
        house_url = base_url + house_url
        house_urls.add(house_url)

In [6]:
# Thu thập toàn bộ url và lưu vào file csv
house_urls = set()

for page in list_page_urls:
    crawl_house_one_page(page)
    
list_house_urls = list(house_urls)
house_urls_df = pd.DataFrame({'URL' : list_house_urls})
house_urls_df.to_csv("HOUSEs_urls.csv", sep = '\t')


In [7]:
houses_df = pd.read_csv('HOUSEs_urls.csv', sep = '\t')
houses_df.head()
len(houses_df)


7617

In [8]:
list_attribute = []
def get_info_house(one_house_url):
    '''
    get house's info from page
        input: house's url
        output: house's data
    '''
    data = {}

    req = s.get(one_house_url, stream=True)
    bs = BeautifulSoup(req.text, 'lxml')
    left_house = bs.findAll('p', class_ = 'left')
    right_house = bs.findAll('p', class_ = 'right')
    address_house = bs.findAll('a', title = 'Quận')
    
     
    list_attributes = []
    for attribute in left_house:
        list_attributes.append(attribute.text.rstrip('\n'))
            
            
    list_values = []
    for value in right_house:
        if value.text != '':
            list_values.append(value.text)
        else:
            check = value['class']
            if any("close" in s for s in check):
                list_values.append('No')
                
            elif any("check" in s for s in check):
                list_values.append('Yes')
    list_address=[]
    for address in address_house:
         list_address.append(address.text)
                    
    for i in range(0, len(list_address)):
        data[list_attributes[i]] = list_values[i]
        data['Quận/Huyện'] = list_address[i]

    return data

In [9]:
#req = s.get('https://rever.vn/mua/can-ho-dao-kim-cuong-tang-trung-don-view-thanh-pho-sam-uat')
#bs = BeautifulSoup(req.text, 'lxml')
#a = bs.find('div', class_ = 'address')
#b = a.find('a', title = 'Quận')
#b.text

In [10]:
list_all_houses = []
i = 0
for house_url in list_house_urls:
    data_dict = {}
    data_dict = get_info_house(house_url)
    i = i + 1
    print(data_dict)
    print('\n', i )
    list_all_houses.append(data_dict)
    

{'Loại hình': 'Căn hộ', 'Quận/Huyện': 'Thủ Đức', 'Phòng ngủ': '2', 'Phòng tắm': '2', 'Diện tích': '79.36 m²', 'Diện tích sử dụng': '79.36 m²', 'Tình hình nội thất': 'Nội thất cơ bản', 'Loại chủ quyền': 'Sổ hồng', 'Dự án': 'Dự án Opal Boulevard', 'Tháp': 'B1', 'Trạng thái': 'Chưa bàn giao', 'Giá bán': '2.89 tỷ', 'Ban công': 'No', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'No', 'Phòng giải trí': 'No', 'Chỗ đậu xe hơi': 'No', 'Hồ bơi riêng': 'No', 'Quầy minibar': 'No', 'Tầng hầm': 'No'}

 1
{'Loại hình': 'Căn hộ', 'Quận/Huyện': 'Quận 4', 'Phòng ngủ': '2', 'Phòng tắm': '2', 'Số tầng': '6', 'Diện tích': '96 m²', 'Diện tích sử dụng': '96 m²', 'Tình hình nội thất': 'Nội thất cơ bản', 'Loại chủ quyền': 'HĐ mua bán', 'Dự án': 'The Pegasuite 1', 'Giá bán': '3.85 tỷ', 'Ban công': 'No', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'No', 'Phòng giải trí': 'No', 'Chỗ đậu xe hơi': 'No', 'Hồ bơi riêng': 'No', 'Quầy minibar': 'No', 'Tầng hầm': 'No', 'Góc làm việc': 'No'}

 2
{'Loại hình': 'Căn hộ', 'Quận/Hu

{'Loại hình': 'Căn hộ', 'Quận/Huyện': 'Quận 8', 'Phòng ngủ': '1', 'Phòng tắm': '1', 'Số tầng': '6', 'Diện tích': '51 m²', 'Diện tích sử dụng': '51 m²', 'Tình hình nội thất': 'Nội thất cơ bản', 'Dự án': 'Ehome 3', 'Giá bán': '1.45 tỷ', 'Ban công': 'No', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'No', 'Phòng giải trí': 'No', 'Chỗ đậu xe hơi': 'No', 'Hồ bơi riêng': 'No', 'Quầy minibar': 'No', 'Tầng hầm': 'No', 'Góc làm việc': 'No', 'Nhà kho': 'No'}

 19
{'Loại hình': 'Căn hộ', 'Quận/Huyện': 'Phú Nhuận', 'Phòng ngủ': '3', 'Phòng tắm': '2', 'Diện tích': '90 m²', 'Diện tích sử dụng': '90 m²', 'Tình hình nội thất': 'Đầy đủ nội thất', 'Dự án': 'The Sun Avenue', 'Tháp': 'Block 2', 'Giá bán': '5.9 tỷ', 'Ban công': 'No', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'No', 'Phòng giải trí': 'No', 'Chỗ đậu xe hơi': 'No', 'Hồ bơi riêng': 'No', 'Quầy minibar': 'No', 'Tầng hầm': 'No', 'Góc làm việc': 'No', 'Nhà kho': 'No'}

 20
{'Loại hình': 'Căn hộ', 'Quận/Huyện': 'Quận 9', 'Phòng ngủ': '2', 'Phòng tắm': '

{'Loại hình': 'Căn hộ', 'Quận/Huyện': 'Quận 2', 'Phòng ngủ': '2', 'Phòng tắm': '2', 'Diện tích': '86.81 m²', 'Tình hình nội thất': 'Đầy đủ nội thất', 'Dự án': 'Citizen Trung Sơn', 'Giá bán': '3.2 tỷ', 'Ban công': 'No', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'No', 'Phòng giải trí': 'No', 'Chỗ đậu xe hơi': 'No', 'Hồ bơi riêng': 'No', 'Quầy minibar': 'No', 'Tầng hầm': 'No', 'Góc làm việc': 'No', 'Nhà kho': 'No', 'Nuôi thú cưng': 'No', 'Gym': 'No'}

 37
{'Loại hình': 'Căn hộ', 'Quận/Huyện': 'Quận 9', 'Phòng ngủ': '2', 'Phòng tắm': '2', 'Diện tích': '75 m²', 'Diện tích sử dụng': '75 m²', 'Tình hình nội thất': 'Nội thất cơ bản', 'Dự án': 'Chung cư Mỹ An - 3G', 'Giá bán': '2.4 tỷ', 'Ban công': 'No', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'No', 'Phòng giải trí': 'No', 'Chỗ đậu xe hơi': 'No', 'Hồ bơi riêng': 'No', 'Quầy minibar': 'No', 'Tầng hầm': 'No', 'Góc làm việc': 'No', 'Nhà kho': 'No', 'Nuôi thú cưng': 'No'}

 38
{'Loại hình': 'Căn hộ', 'Quận/Huyện': 'Quận 8', 'Phòng ngủ': '2', 'Phòng

{'Loại hình': 'Căn hộ', 'Quận/Huyện': 'Quận 4', 'Phòng ngủ': '2', 'Phòng tắm': '2', 'Diện tích': '79.8 m²', 'Tình hình nội thất': 'Đầy đủ nội thất', 'Mục đích sử dụng': 'để ở hoặc cho thuê', 'Loại chủ quyền': 'HĐ mua bán', 'Dự án': 'Vinhomes Central Park', 'Giá bán': '4.3 tỷ', 'Thời gian bắt đầu bán': '04/01/2018', 'Ban công': 'Yes', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'No', 'Phòng giải trí': 'Yes', 'Chỗ đậu xe hơi': 'Yes', 'Hồ bơi riêng': 'Yes', 'Quầy minibar': 'No', 'Tầng hầm': 'No', 'Góc làm việc': 'Yes'}

 55
{'Loại hình': 'Căn hộ', 'Quận/Huyện': 'Quận 7', 'Phòng ngủ': '2', 'Phòng tắm': '1', 'Diện tích': '58 m²', 'Diện tích sử dụng': '54 m²', 'Tình hình nội thất': 'Đầy đủ nội thất', 'Loại chủ quyền': 'HĐ mua bán', 'Dự án': 'Vinhomes Grand Park', 'Tháp': 'S1.07', 'Giá bán': '2.3 tỷ', 'Ban công': 'No', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'No', 'Phòng giải trí': 'No', 'Chỗ đậu xe hơi': 'No', 'Hồ bơi riêng': 'No', 'Quầy minibar': 'No', 'Tầng hầm': 'No', 'Góc làm việc': 'No'}


{'Loại hình': 'Biệt thự', 'Quận/Huyện': 'Quận 2', 'Số tầng': '2', 'Diện tích': '99.9 m²', 'Chiều dài': '17 m', 'Diện tích sử dụng': '450 m²', 'Chiều rộng': '8 m', 'Diện tích sàn': '292.4 m²', 'Tình hình nội thất': 'Nội thất cơ bản', 'Loại chủ quyền': 'Sổ hồng', 'Giá bán': '23 tỷ', 'Ban công': 'No', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'No', 'Phòng giải trí': 'No', 'Chỗ đậu xe hơi': 'No', 'Hồ bơi riêng': 'No', 'Quầy minibar': 'No', 'Tầng hầm': 'No', 'Góc làm việc': 'No'}

 74
{'Loại hình': 'Căn hộ', 'Quận/Huyện': 'Quận 7', 'Phòng ngủ': '2', 'Phòng tắm': '2', 'Diện tích': '69 m²', 'Diện tích sử dụng': '63.5 m²', 'Tình hình nội thất': 'Không có nội thất', 'Loại chủ quyền': 'HĐ mua bán', 'Dự án': 'Vinhomes Grand Park', 'Tháp': 'S3.03', 'Giá bán': '3.25 tỷ', 'Ban công': 'No', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'No', 'Phòng giải trí': 'No', 'Chỗ đậu xe hơi': 'No', 'Hồ bơi riêng': 'No', 'Quầy minibar': 'No', 'Tầng hầm': 'No', 'Góc làm việc': 'No'}

 75
{'Loại hình': 'Căn hộ', 'Quận/

...

{'Loại hình': 'Căn hộ', 'Quận/Huyện': 'Quận 4', 'Phòng ngủ': '2', 'Phòng tắm': '2', 'Diện tích': '78.52 m²', 'Diện tích sử dụng': '78.52 m²', 'Tình hình nội thất': 'Nội thất cơ bản', 'Loại chủ quyền': 'HĐ mua bán', 'Dự án': 'Saigon Mia', 'Giá bán': '4.1 tỷ', 'Ban công': 'No', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'No', 'Phòng giải trí': 'No', 'Chỗ đậu xe hơi': 'No', 'Hồ bơi riêng': 'No', 'Quầy minibar': 'No', 'Tầng hầm': 'No', 'Góc làm việc': 'No', 'Nhà kho': 'No'}

 7536
{'Loại hình': 'Căn hộ', 'Quận/Huyện': 'Quận 7', 'Phòng ngủ': '1', 'Phòng tắm': '1', 'Diện tích': '54 m²', 'Diện tích sử dụng': '51 m²', 'Tình hình nội thất': 'Đầy đủ nội thất', 'Loại chủ quyền': 'HĐ mua bán', 'Dự án': 'Masteri An Phú', 'Tháp': 'Tower A', 'Trạng thái': 'Chưa bàn giao', 'Giá bán': '3.15 tỷ', 'Ban công': 'No', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'No', 'Phòng giải trí': 'No', 'Chỗ đậu xe hơi': 'No', 'Hồ bơi riêng': 'No', 'Quầy minibar': 'No', 'Tầng hầm': 'No'}

 7537
{'Loại hình': 'Căn hộ', 'Quận/

{'Loại hình': 'Căn hộ', 'Quận/Huyện': 'Nhà Bè', 'Phòng ngủ': '2', 'Phòng tắm': '2', 'Diện tích': '77 m²', 'Diện tích sử dụng': '77 m²', 'Tình hình nội thất': 'Đầy đủ nội thất', 'Loại chủ quyền': 'Sổ hồng', 'Dự án': 'Lux Garden', 'Giá bán': '2.58 tỷ', 'Ban công': 'No', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'No', 'Phòng giải trí': 'No', 'Chỗ đậu xe hơi': 'No', 'Hồ bơi riêng': 'No', 'Quầy minibar': 'No', 'Tầng hầm': 'No', 'Góc làm việc': 'No', 'Nhà kho': 'No'}

 7553
{'Loại hình': 'Căn hộ', 'Quận/Huyện': 'Nhà Bè', 'Phòng ngủ': '2', 'Phòng tắm': '2', 'Số tầng': '14', 'Diện tích': '77.8 m²', 'Diện tích sử dụng': '72.9 m²', 'Tình hình nội thất': 'Nội thất cơ bản', 'Loại chủ quyền': 'HĐ mua bán', 'Dự án': 'Ricca', 'Tháp': 'BLOCK A', 'Trạng thái': 'Chưa bàn giao', 'Giá bán': '2.83 tỷ', 'Ban công': 'No', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'No', 'Phòng giải trí': 'No', 'Chỗ đậu xe hơi': 'No', 'Hồ bơi riêng': 'No', 'Quầy minibar': 'No'}

 7554
{'Loại hình': 'Căn hộ', 'Quận/Huyện': 'Bình 

{'Loại hình': 'Căn hộ', 'Quận/Huyện': 'Nhà Bè', 'Phòng ngủ': '2', 'Phòng tắm': '2', 'Diện tích': '65 m²', 'Tình hình nội thất': 'Đầy đủ nội thất', 'Mục đích sử dụng': 'Ở', 'Loại chủ quyền': 'HĐ mua bán', 'Dự án': 'Masteri Thảo Điền', 'Giá bán': '3.4 tỷ', 'Thời gian bắt đầu bán': '21/02/2017', 'Ban công': 'Yes', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'No', 'Phòng giải trí': 'Yes', 'Chỗ đậu xe hơi': 'Yes', 'Hồ bơi riêng': 'Yes', 'Quầy minibar': 'No', 'Tầng hầm': 'No', 'Góc làm việc': 'No'}

 7571
{'Mã nhà đất': 'MBX4202', 'Quận/Huyện': 'Bình Thạnh'}

 7572
{'Loại hình': 'Căn hộ', 'Quận/Huyện': 'Quận 2', 'Phòng ngủ': '2', 'Phòng tắm': '2', 'Diện tích': '55.86 m²', 'Diện tích sử dụng': '50 m²', 'Tình hình nội thất': 'Không có nội thất', 'Dự án': 'Saigon Intela', 'Tháp': 'A', 'Giá bán': '1.44 tỷ', 'Ban công': 'No', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'No', 'Phòng giải trí': 'No', 'Chỗ đậu xe hơi': 'No', 'Hồ bơi riêng': 'No', 'Quầy minibar': 'No', 'Tầng hầm': 'No', 'Góc làm việc': 'No

{'Loại hình': 'Căn hộ', 'Quận/Huyện': 'Quận 9', 'Phòng ngủ': '1', 'Phòng tắm': '1', 'Diện tích': '48.5 m²', 'Diện tích sử dụng': '44.2 m²', 'Tình hình nội thất': 'Đầy đủ nội thất', 'Loại chủ quyền': 'HĐ mua bán', 'Dự án': 'Lexington Residence', 'Tháp': 'LA', 'Giá bán': '2.35 tỷ', 'Ban công': 'No', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'No', 'Phòng giải trí': 'No', 'Chỗ đậu xe hơi': 'No', 'Hồ bơi riêng': 'No', 'Quầy minibar': 'No', 'Tầng hầm': 'No', 'Góc làm việc': 'No'}

 7589
{'Loại hình': 'Căn hộ', 'Quận/Huyện': 'Quận 7', 'Phòng ngủ': '2', 'Phòng tắm': '2', 'Diện tích': '73.4 m²', 'Diện tích sử dụng': '67.5 m²', 'Tình hình nội thất': 'Đầy đủ nội thất', 'Loại chủ quyền': 'HĐ mua bán', 'Dự án': 'The Sun Avenue', 'Tháp': 'Block 1', 'Giá bán': '3.6 tỷ', 'Ban công': 'No', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'No', 'Phòng giải trí': 'No', 'Chỗ đậu xe hơi': 'No', 'Hồ bơi riêng': 'No', 'Quầy minibar': 'No', 'Tầng hầm': 'No', 'Góc làm việc': 'No'}

 7590
{'Loại hình': 'Căn hộ', 'Quận/H

{'Loại hình': 'Nhà phố', 'Quận/Huyện': 'Bình Chánh', 'Phòng ngủ': '4', 'Phòng tắm': '5', 'Số tầng': '3', 'Diện tích': '36 m²', 'Diện tích sử dụng': '112 m²', 'Tình hình nội thất': 'Nội thất cơ bản', 'Loại chủ quyền': 'Sổ hồng', 'Giá bán': '6.5 tỷ', 'Ban công': 'No', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'No', 'Phòng giải trí': 'No', 'Chỗ đậu xe hơi': 'No', 'Hồ bơi riêng': 'No', 'Quầy minibar': 'No', 'Tầng hầm': 'No', 'Góc làm việc': 'No', 'Nhà kho': 'No'}

 7607
{'Mã nhà đất': 'MBW8070', 'Quận/Huyện': 'Tân Phú', 'Giá đăng': '3.8 tỷ', 'Loại hình nhà đất': 'Nhà phố', 'Số phòng ngủ': '2', 'Số phòng tắm': '2', 'Diện tích': '39'}

 7608
{'Loại hình': 'Căn hộ', 'Quận/Huyện': 'Nhà Bè', 'Phòng ngủ': '2', 'Phòng tắm': '1', 'Diện tích': '77 m²', 'Diện tích sử dụng': '77 m²', 'Tình hình nội thất': 'Không có nội thất', 'Loại chủ quyền': 'HĐ mua bán', 'Dự án': 'Jamila Khang Điền', 'Giá bán': '2.75 tỷ', 'Ban công': 'No', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'No', 'Phòng giải trí': 'No', 'Chỗ 

In [11]:
len(list_all_houses)

7617

In [12]:
# all_houses_df = pd.DataFrame(list_all_houses)
all_houses_df = pd.DataFrame.from_dict(list_all_houses)
all_houses_df.shape


(7617, 42)

In [13]:
all_houses_df.to_csv("HOUSEs_info.csv", sep = '\t', index = False)
all_houses_df

Loại hình Quận/Huyện Phòng ngủ Phòng tắm Diện tích Diện tích sử dụng  \
0        Căn hộ    Thủ Đức         2         2  79.36 m²          79.36 m²   
1        Căn hộ     Quận 4         2         2     96 m²             96 m²   
2        Căn hộ     Quận 7         2         2  67.37 m²               NaN   
3        Căn hộ     Quận 2         1         1   50.6 m²           50.6 m²   
4        Căn hộ     Quận 7         2         1     57 m²             57 m²   
...         ...        ...       ...       ...       ...               ...   
7612  Shophouse     Quận 6         3         2    122 m²            122 m²   
7613     Căn hộ     Quận 7         2         2  56.98 m²          56.98 m²   
7614     Căn hộ     Quận 7         2         2     80 m²             80 m²   
7615     Căn hộ     Quận 9         2         2   64.5 m²           64.5 m²   
7616     Căn hộ     Quận 2         3         3    155 m²            155 m²   

     Tình hình nội thất Loại chủ quyền                  Dự án        Tháp  \
0       Nội thất cơ bản        Sổ hồng   Dự án Opal Boulevard          B1   
1       Nội thất cơ bản     HĐ mua bán        The Pegasuite 1         NaN   
2       Nội thất cơ bản     HĐ mua bán    Q7 Saigon Riverside      URANUS   
3       Nội thất cơ bản     HĐ mua bán  Vinhomes Golden River  The Aqua 1   
4     Không có nội thất        Sổ hồng           Riverside 90         NaN   
...                 ...            ...                    ...         ...   
7612    Đầy đủ nội thất            NaN                The Art         NaN   
7613    Nội thất cơ bản            NaN           Q7 Boulevard          B1   
7614    Nội thất cơ bản     HĐ mua bán                Hausneo         NaN   
7615    Nội thất cơ bản     HĐ mua bán       Victoria Village         NaN   
7616    Nội thất cơ bản     HĐ mua bán          Riviera Point    THE VIEW   

      ...  Gym Bàn ghế phòng khách Chiều dài Chiều rộng Diện tích sàn   TV  \
0     ...  NaN                 NaN       NaN        NaN           NaN  NaN   
1     ...  NaN                 NaN       NaN        NaN           NaN  NaN   
2     ...  NaN                 NaN       NaN        NaN           NaN  NaN   
3     ...  NaN                 NaN       NaN        NaN           NaN  NaN   
4     ...  NaN                 NaN       NaN        NaN           NaN  NaN   
...   ...  ...                 ...       ...        ...           ...  ...   
7612  ...  NaN                 NaN       NaN        NaN           NaN  NaN   
7613  ...  NaN                 NaN       NaN        NaN           NaN  NaN   
7614  ...  NaN                 NaN       NaN        NaN           NaN  NaN   
7615  ...  NaN                 NaN       NaN        NaN           NaN  NaN   
7616  ...  NaN                 NaN       NaN        NaN           NaN  NaN   

     Máy hút mùi Kệ TV Cảm biến cháy Tủ lạnh  
0            NaN   NaN           NaN     NaN  
1            NaN   NaN           NaN     NaN  
2            NaN   NaN           NaN     NaN  
3            NaN   NaN           NaN     NaN  
4            NaN   NaN           NaN     NaN  
...          ...   ...           ...     ...  
7612         NaN   NaN           NaN     NaN  
7613         NaN   NaN           NaN     NaN  
7614         NaN   NaN           NaN     NaN  
7615         NaN   NaN           NaN     NaN  
7616         NaN   NaN           NaN     NaN  

[7617 rows x 42 columns]